## CCF-API Documentation

### INDEX
1. [Installation](#install)
2. [Imports](#imports)
3. [Configuration](#config)
4. [Methods](#methods)
    1. [Database Check](#db_status)
    2. [Run a Sparql query](#sparql_get)
    3. [Run a Sparql query (POST)](#sparql_post)
    4. [Get aggregate results / statistics](#agg_results)
    5. [get Spatial Placement Request](#spatial_entity)
    6. [Get all hubmap rui locations](#rui_loc) 
    7. [Get number of ontology term occurrences for a search](#ontology_term)
    8. [Get number of cell type term occurrences for a search](#cell_term_occ)
    9. [Get ontology term tree nodes](#ontology_nodes)
    10. [Get cell type tree nodes](#cell_nodes)
    11. [Get tissue provider names (for filtering)](#providers)
    12. [Get all reference organs](#ref_organs)
    13. [Get all nodes to form the 3D scene for an organ](#3d_scene)
    14. [Get all nodes to form the 3D scene of reference body, organs, and tissues](#nodes_3d)
    15. [Get technology names (for filtering)](#tech)
    16. [Get Tissue Block Results](#tissue_block)
    17. [Get all GTEx rui locations (if enabled)](#gtex_rui)
    18. [Token](#token_usage)
    

***
[Click here](https://observablehq.com/@cns-iu/ccf-api-documentation-javascript) to view the documentation for ccf-api javascript module.  


<a id='install'></a>
### Installation

#### ccf-openapi can be installed via `pip` from [PyPI](https://pypi.org/project/ccf-openapi/#description).
***
> `pip install ccf-openapi`
***

<a id='imports'></a>
### Imports

We import the ccf-openapi as follows:

In [1]:
import ccf_openapi_client

Although we can use ccf_openapi_client for all our tasks, it is easier if we have individual imports as follows:

In [2]:
from ccf_openapi_client.api import default_api
from ccf_openapi_client.model.aggregate_count import AggregateCount
from ccf_openapi_client.model.database_status import DatabaseStatus
from ccf_openapi_client.model.error_message import ErrorMessage
from ccf_openapi_client.model.flat_spatial_placement import FlatSpatialPlacement
from ccf_openapi_client.model.get_spatial_placement_request import GetSpatialPlacementRequest
from ccf_openapi_client.model.min_max import MinMax
from ccf_openapi_client.model.ontology_tree import OntologyTree
from ccf_openapi_client.model.sparql_query_request import SparqlQueryRequest
from ccf_openapi_client.model.spatial_entity import SpatialEntity
from ccf_openapi_client.model.spatial_scene_node import SpatialSceneNode
from ccf_openapi_client.model.spatial_search import SpatialSearch
from ccf_openapi_client.model.tissue_block import TissueBlock

For the purposes of this documentation we need some other libraries imported here: 

In [3]:
import time
from pprint import pprint

<a id='config'></a>
### Configuration
ccf-openapi can fetch data from 
> HRA-API: https://apps.humanatlas.io/hra-api/v1 <br> 
> Staging Server: https://apps.humanatlas.io/hra-api--staging/v1 <br>
> You could also use any other instance that you decide to host our code on

You can get more information about our APIs [here](https://apps.humanatlas.io/hra-api/#/).

You'll need to point the host in the configuration to one of the links: 

In [4]:
configuration = ccf_openapi_client.Configuration(
    host = "https://apps.humanatlas.io/hra-api/v1"
)

<a id='api'></a>
### Creating the API Instance
We will need to create an instance of ApiClient from ccf_openapi_client. The configuration we created above will be passed as a parameter for the constructor. <br> <br>
Using the instance of ApiClient we create an instance of DefaultApi from the default_api module we imported above. This instance represents the API interface and provides methods to interact with the API endpoints defined in the OpenAPI specification.

In [5]:
api_client = ccf_openapi_client.ApiClient(configuration)

api_instance = default_api.DefaultApi(api_client)

<a id='methods'></a>
### Methods

ccf_openapi_client provides multiple methods which we have described below. Each method is described in more detail below : 

***
<a id='db_status'></a>
#### Database Status
On first run the database might take some time to be ready, so we run it on loop and wait until it's ready.
<pre>
Accepted Parameters:
    token - (string) (optional)
</pre>
***
> You can still use the other methods without waiting for the database to be ready, but the initial requests might take a little longer.

In [6]:
db_ready = False
result = None
while not db_ready:
    result = api_instance.db_status()
    if result['status'] == 'Ready':
        db_ready = True
    else:
        print('Database not ready yet! Retrying...', result)
        time.sleep(2)
print('Database ready!\n', result)

Database ready!
 {'checkback': 3600000,
 'load_time': 10330,
 'message': 'Database successfully loaded',
 'status': 'Ready'}


***
<a id='sparql_get'></a>
#### Run a SPARQL query
<pre>
Accepted Parameters: 
    token - (string) (optional)
    format - (string) (optional) (use only application/json in format, any other formats will result in errors.)
    query - (string) (required)
</pre>

In [7]:
try:
    api_response = api_instance.sparql(query='SELECT * WHERE { ?sub ?pred ?obj . } LIMIT 10', format='application/json')
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

[{'obj': 'http://www.w3.org/2002/07/owl#Ontology',
  'pred': 'http://www.w3.org/1999/02/22-rdf-syntax-ns#type',
  'sub': 'http://purl.org/ccf/ccf.owl'},
 {'obj': 'http://purl.org/ccf/releases/2.1.0/ccf.owl',
  'pred': 'http://www.w3.org/2002/07/owl#versionIRI',
  'sub': 'http://purl.org/ccf/ccf.owl'},
 {'obj': '"The Common Coordinate Framework (CCF) Ontology is an application '
         'ontology built to support the development of the Human Reference '
         'Atlas (HRA).  It unifies vocabulary for HRA construction and '
         'usage—making it possible to ingest external data sources; supporting '
         'uniform tissue sample registration that includes the spatial '
         'positioning and semantic annotations within 3D reference organs; and '
         'supporting user-formulated cross-domain queries over tissue donor '
         'properties, anatomical structures, cell types, biomarkers, and 3D '
         'space. The CCF Ontology consists of three major ontologies. The '
  

***
<a id='sparql_post'></a>
#### Run a SPARQL query (POST)
<pre>
Accepted Parameters:
    token - (string) (optional)
    format - (string) (optional) (use only application/json in format, any other formats will result in errors.)
    sparql_query_request - { "query": "" } (required)
</pre>

In [8]:
request = {"query": "SELECT * WHERE { ?sub ?pred ?obj . } LIMIT 10"}
# use only application/json in format, any other formats will result in errors.
try:
    # Get aggregate results / statistics
    api_response = api_instance.sparql_post(sparql_query_request=request, format='application/json')
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

[{'obj': 'http://www.w3.org/2002/07/owl#Ontology',
  'pred': 'http://www.w3.org/1999/02/22-rdf-syntax-ns#type',
  'sub': 'http://purl.org/ccf/ccf.owl'},
 {'obj': 'http://purl.org/ccf/releases/2.1.0/ccf.owl',
  'pred': 'http://www.w3.org/2002/07/owl#versionIRI',
  'sub': 'http://purl.org/ccf/ccf.owl'},
 {'obj': '"The Common Coordinate Framework (CCF) Ontology is an application '
         'ontology built to support the development of the Human Reference '
         'Atlas (HRA).  It unifies vocabulary for HRA construction and '
         'usage—making it possible to ingest external data sources; supporting '
         'uniform tissue sample registration that includes the spatial '
         'positioning and semantic annotations within 3D reference organs; and '
         'supporting user-formulated cross-domain queries over tissue donor '
         'properties, anatomical structures, cell types, biomarkers, and 3D '
         'space. The CCF Ontology consists of three major ontologies. The '
  

***
<a id='agg_results'></a>
#### Get aggregate results / statistics
<pre>
Accepted Parameters:
    age - (MinMax) (optional) (min = 1.0; max = 110.0)
    bmi - (MinMax) (optional) (min = 13.0; max = 83.0)
    cache - (boolean)  (optional) (defaults to True)
    sex - (string)  (optional) (male, female, both)
    technologies - (string) (optional) (List of technologies - api_instance.technology_names)
    providers - (string) (optional) 
    ontology_terms - (string) (optional) 
    cell_type_terms - (string) (optional) 
    spatial - SpatialSearch(x, y, z, radius, target) (optional) 
    token - (string) (optional) 
</pre>

In [9]:
age = MinMax(min=45.0, max=60.0)
bmi = MinMax(min=65.0, max=83.0)
cache = True
sex = "female"
technologies = []
providers = []
ontology_terms = ["http://purl.obolibrary.org/obo/UBERON_0000955",]
cell_type_terms = ["http://purl.obolibrary.org/obo/CL_0000000",] 
spatial = [SpatialSearch(
            x=84.0,
            y=146.0,
            z=53.0,
            radius=12.0,
            target="http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain",
        ),]
token = ""

try:
    api_response = api_instance.aggregate_results(age=age, bmi=bmi, cache=cache, ontology_terms=ontology_terms, cell_type_terms=cell_type_terms, providers=providers, sex=sex, spatial=spatial, technologies=technologies, token=token)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

[{'count': 2.0, 'label': 'Tissue Data Providers'},
 {'count': 3.0, 'label': 'Donors'},
 {'count': 6.0, 'label': 'Tissue Blocks'},
 {'count': 0.0, 'label': 'Tissue Sections'},
 {'count': 6.0, 'label': 'Tissue Datasets'}]


In [ ]:
***
<a id='spatial_entity'></a>
#### Given a SpatialEntity already placed relative to a reference SpatialEntity retrieve a new direct SpatialPlacement to the given SpatialEntity IRI
More Info : https://apps.humanatlas.io/hra-api/#/operations/get-spatial-placement
<pre>
Accepted Parameters:
    get_spatial_placement_request = {
        "target_iri": (string) (required)
        "rui_location": {
            A Spatial Entity defines a bounded cartesian space and the units it is measured in.
            It typically represents a real world thing, e.g., a human body, a human kidney, a tissue section,
            or an individual cell.
            
            "@id": string<uri> (required)
            "@type": (string) (required) (allowed value: SpatialEntity)
            
            "entityId": string<uri> (optional) (Identifier of the entity the spatial object represents)
            "ccf_annotations": array[string]<uri> (optional) (Annotations attached to the entity.)
            "representation_of": string<uri> (optional) (Identifier for the item the spatial object represents.)
            "reference_organ": string<uri> (optional) (Identifier for the organ the spatial object represents.)
            
            "creator": (string) (optional)
            "creator_first_name": (string) (optional)
            "creator_last_name": (string) (optional)
            "creator_orcid": (string) (optional)
            "creation_date": (string)<date>,
            
            "x_dimension": (number) (required),
            "y_dimension": (number) (required),
            "z_dimension": (number) (required),
            "dimension_units": (string) (required) (default: millimeters),
            
            "label": (string) (optional)
            "comment": (string) (optional)
            "rui_rank": (integer) (optional)
            "sex": (string) (optional)
            "side": (string) (optional) (Used for organs that come in pairs to distinguish between them, i.e. kidneys, etc)
            "slice_count": (integer) (optional)
            "slice_thickness": (number) (optional)
            
            
            "placement": {
                "@id": (string) (required),
                "@type": (string) (required) (allowed value: SpatialEntity),
                "placement_date": string<date>,
                "x_translation": (number) (required),
                "y_translation": (number) (required),
                "z_translation": (number) (required),
                "translation_units": (number) (required) (allowed value: millimeters),
                "x_rotation": (number) (required),
                "y_rotation": (number) (required),
                "z_rotation": (number) (required),
                "rotation_units": (string) (required) (allowed value: degree),
                "x_scaling": (number) (required),
                "y_scaling": (number) (required),
                "z_scaling": (number)  (optional),
                "scaling_units": (string) (required) (allowed value: degree),
                "target": (string) (required),
        }
            
        }
    }
</pre>

In [10]:
get_spatial_placement_request = {
    "target_iri": "http://purl.org/ccf/latest/ccf.owl#VHFemale",
    "rui_location": {
        "@id": "http://purl.org/ccf/1.5/f7130161-ad0a-4801-b5a4-f6297e0f1869",
        "@type": "SpatialEntity",
        "creator": "Bruce Herr",
        "creator_first_name": "Bruce",
        "creator_last_name": "Herr",
        "creation_date": "2022-04-27",
        "ccf_annotations": ["http://purl.obolibrary.org/obo/UBERON_0002015", "http://purl.obolibrary.org/obo/UBERON_0000362", "http://purl.obolibrary.org/obo/UBERON_0004200", "http://purl.obolibrary.org/obo/UBERON_0001225", "http://purl.obolibrary.org/obo/UBERON_0001284", "http://purl.obolibrary.org/obo/UBERON_0002189"],
        "x_dimension": 11,
        "y_dimension": 12,
        "z_dimension": 13,
        "dimension_units": "millimeter",
        "placement": {
            "@id": "http://purl.org/ccf/1.5/f7130161-ad0a-4801-b5a4-f6297e0f1869_placement",
            "@type": "SpatialPlacement",
            "target": "http://purl.org/ccf/latest/ccf.owl#VHFLeftKidneyV1.1",
            "placement_date": "2022-04-27",
            "x_scaling": 1,
            "y_scaling": 1,
            "z_scaling": 1,
            "scaling_units": "ratio",
            "x_rotation": -61,
            "y_rotation": 50,
            "z_rotation": -84,
            "rotation_order": "XYZ",
            "rotation_units": "degree",
            "x_translation": 20.149,
            "y_translation": 109.963,
            "z_translation": 38.79,
            "translation_units": "millimeter"
        }
    }
}
try:
    # Get aggregate results / statistics
    api_response = api_instance.get_spatial_placement(get_spatial_placement_request)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

{'@context': 'https://hubmapconsortium.github.io/hubmap-ontology/ccf-context.jsonld',
 '@id': 'http://purl.org/ccf/1.5/b198d381-293b-4451-bb02-ed40bf1cbf29_placement',
 '@type': 'SpatialPlacement',
 'placement_date': datetime.date(2023, 6, 2),
 'rotation_order': 'XYZ',
 'rotation_units': 'degree',
 'scaling_units': 'ratio',
 'source': 'http://purl.org/ccf/1.5/f7130161-ad0a-4801-b5a4-f6297e0f1869',
 'target': 'http://purl.org/ccf/latest/ccf.owl#VHFemale',
 'translation_units': 'millimeter',
 'x_rotation': -61.0,
 'x_scaling': 1.0,
 'x_translation': 60.20057,
 'y_rotation': 50.0,
 'y_scaling': 1.0,
 'y_translation': 285.73913899999997,
 'z_rotation': -84.0,
 'z_scaling': 1.0,
 'z_translation': -100.59638600000001}


***
<a id='rui_loc'></a>
#### Get all hubmap rui locations (if enabled)
<pre>
Accepted Parameters:
    cache - (boolean) (optional)
    token - (string) (optional)
</pre>

In [11]:
try:
    api_response = api_instance.gtex_rui_locations(cache = True)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

{'@context': {'@base': 'http://purl.org/ccf/latest/ccf-entity.owl#',
              '@vocab': 'http://purl.org/ccf/latest/ccf-entity.owl#',
              'ccf': 'http://purl.org/ccf/latest/ccf.owl#',
              'cellTypeTerms': {'@id': 'has_cell_type_term', '@type': '@id'},
              'datasets': {'@id': 'has_dataset', '@type': '@id'},
              'description': 'rdfs:comment',
              'label': 'rdfs:label',
              'link': {'@id': 'rdfs:seeAlso', '@type': '@id'},
              'ontologyTerms': {'@id': 'has_ontology_term', '@type': '@id'},
              'rdfs': 'http://www.w3.org/2000/01/rdf-schema#',
              'rui_location': {'@id': 'has_spatial_entity', '@type': '@id'},
              'samples': {'@reverse': 'has_donor'},
              'sections': {'@id': 'has_tissue_section', '@type': '@id'},
              'thumbnail': {'@id': 'has_thumbnail'}},
 '@graph': [{'@id': 'https://gtexportal.org/home/tissue/Breast#FDonors',
             '@type': 'Donor',
            

***
<a id='ontology_term'></a>
#### Get number of ontology term occurrences for a search
<pre>
Accepted Parameters:
    age - (MinMax) (optional) (min = 1.0; max = 110.0)
    bmi - (MinMax) (optional) (min = 13.0; max = 83.0)
    cache - (boolean)  (optional) (defaults to True)
    sex - (string)  (optional) (male, female, both)
    technologies - (string) (optional) (List of technologies - api_instance.technology_names)
    providers - (string) (optional) 
    ontology_terms - (string) (optional) 
    cell_type_terms - (string) (optional) 
    spatial - SpatialSearch(x, y, z, radius, target) (optional) 
    token - (string) (optional) 
</pre>

In [12]:
age = MinMax(min=45.0, max=60.0)
bmi = MinMax(min=65.0, max=83.0)
cache = True
sex = "female"
technologies = []
providers = []
ontology_terms = ["http://purl.obolibrary.org/obo/UBERON_0000955",]
cell_type_terms = ["http://purl.obolibrary.org/obo/CL_0000000",] 
spatial = [SpatialSearch(
            x=84.0,
            y=146.0,
            z=53.0,
            radius=12.0,
            target="http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain",
        ),]
token = ""

try:
    api_response = api_instance.ontology_term_occurences(age=age, bmi=bmi, cache=cache, ontology_terms=ontology_terms, cell_type_terms=cell_type_terms, providers=providers, sex=sex, spatial=spatial, technologies=technologies, token=token)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

{'http://purl.obolibrary.org/obo/UBERON_0000955': 6,
 'http://purl.obolibrary.org/obo/UBERON_0002581': 5,
 'http://purl.obolibrary.org/obo/UBERON_0002661': 4,
 'http://purl.obolibrary.org/obo/UBERON_0002703': 5,
 'http://purl.obolibrary.org/obo/UBERON_0002771': 1,
 'http://purl.obolibrary.org/obo/UBERON_0002813': 5,
 'http://purl.obolibrary.org/obo/UBERON_0006093': 1,
 'http://purl.obolibrary.org/obo/UBERON_0013702': 6,
 'http://purl.obolibrary.org/obo/UBERON_0035932': 4}


***
<a id='cell_term_occ'></a>
#### Get number of cell type term occurrences for a search
<pre>
Accepted Parameters:
    age - (MinMax) (optional) (min = 1.0; max = 110.0)
    bmi - (MinMax) (optional) (min = 13.0; max = 83.0)
    cache - (boolean)  (optional) (defaults to True)
    sex - (string)  (optional) (male, female, both)
    technologies - (string) (optional) (List of technologies - api_instance.technology_names)
    providers - (string) (optional) 
    ontology_terms - (string) (optional) 
    cell_type_terms - (string) (optional) 
    spatial - SpatialSearch(x, y, z, radius, target) (optional) 
    token - (string) (optional) 
</pre>

In [13]:
age = MinMax(min=45.0, max=60.0)
bmi = MinMax(min=65.0, max=83.0)
cache = True
sex = "female"
technologies = []
providers = []
ontology_terms = ["http://purl.obolibrary.org/obo/UBERON_0000955",]
cell_type_terms = ["http://purl.obolibrary.org/obo/CL_0000000",] 
spatial = [SpatialSearch(
            x=84.0,
            y=146.0,
            z=53.0,
            radius=12.0,
            target="http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain",
        ),]
token = ""

try:
    api_response = api_instance.cell_type_term_occurences(age=age, bmi=bmi, cache=cache, ontology_terms=ontology_terms, cell_type_terms=cell_type_terms, providers=providers, sex=sex, spatial=spatial, technologies=technologies, token=token)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

{'http://purl.obolibrary.org/obo/CL_0000000': 6,
 'http://purl.obolibrary.org/obo/PCL_0015001': 6,
 'http://purl.obolibrary.org/obo/PCL_0015002': 6,
 'http://purl.obolibrary.org/obo/PCL_0015003': 6,
 'http://purl.obolibrary.org/obo/PCL_0015004': 6,
 'http://purl.obolibrary.org/obo/PCL_0015005': 6,
 'http://purl.obolibrary.org/obo/PCL_0015006': 6,
 'http://purl.obolibrary.org/obo/PCL_0015007': 6,
 'http://purl.obolibrary.org/obo/PCL_0015008': 6,
 'http://purl.obolibrary.org/obo/PCL_0015009': 6,
 'http://purl.obolibrary.org/obo/PCL_0015010': 6,
 'http://purl.obolibrary.org/obo/PCL_0015011': 6,
 'http://purl.obolibrary.org/obo/PCL_0015012': 6,
 'http://purl.obolibrary.org/obo/PCL_0015013': 6,
 'http://purl.obolibrary.org/obo/PCL_0015014': 6,
 'http://purl.obolibrary.org/obo/PCL_0015015': 6,
 'http://purl.obolibrary.org/obo/PCL_0015016': 6,
 'http://purl.obolibrary.org/obo/PCL_0015017': 6,
 'http://purl.obolibrary.org/obo/PCL_0015018': 6,
 'http://purl.obolibrary.org/obo/PCL_0015019': 6,
 

***
<a id='ontology_nodes'></a>
#### Get ontology term tree nodes
<pre>
Accepted Parameters:
    cache - (boolean) (optional)
    token - (string) (optional)
</pre>

In [14]:
try:
    api_response = api_instance.ontology_tree_model(cache=True)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

{'nodes': {'http://purl.obolibrary.org/obo/UBERON_0000002': {'@id': 'http://purl.obolibrary.org/obo/UBERON_0000002',
                                                             '@type': 'OntologyTreeNode',
                                                             'children': ['http://purl.obolibrary.org/obo/UBERON_0000458',
                                                                          'http://purl.obolibrary.org/obo/UBERON_0004801',
                                                                          'http://purl.obolibrary.org/obo/UBERON_0012247',
                                                                          'http://purl.obolibrary.org/obo/UBERON_0012249',
                                                                          'http://purl.obolibrary.org/obo/UBERON_0013761',
                                                                          'https://purl.org/ccf/ASCTB-TEMP_cervical-mucosa',
                                                     

***
<a id='cell_nodes'></a>
#### Get cell type tree nodes
<pre>
Accepted Parameters:
    cache - (boolean) (optional)
    token - (string) (optional)
</pre>

In [15]:
try:
    api_response = api_instance.cell_type_tree_model(cache = False)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

{'nodes': {'http://purl.obolibrary.org/obo/CL_0000000': {'@id': 'http://purl.obolibrary.org/obo/CL_0000000',
                                                         '@type': 'OntologyTreeNode',
                                                         'children': ['http://purl.obolibrary.org/obo/CL_0000212',
                                                                      'http://purl.obolibrary.org/obo/CL_0002071',
                                                                      'http://purl.obolibrary.org/obo/CL_0002521',
                                                                      'http://purl.obolibrary.org/obo/CL_1000309',
                                                                      'https://purl.org/ccf/ASCTB-TEMP_adventitial-stromal-cell',
                                                                      'http://purl.obolibrary.org/obo/CL_1001096',
                                                                      'https://purl.org/ccf/ASCTB-TE

***
<a id='providers'></a>
#### Get tissue provider names (for filtering)
<pre>
Accepted Parameters:
    cache - (boolean) (optional)
    token - (string) (optional)
</pre>

In [16]:
try:
    api_response = api_instance.provider_names(cache = True)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

['Allen Institute',
 'GTEx Project',
 'KPMP-IU/OSU',
 'RTI-General Electric',
 'SEA-AD',
 'SPARC-UCLA',
 'TMC-CalTech',
 'TMC-Florida',
 'TMC-Stanford',
 'TMC-UCSD',
 'TMC-UConn',
 'TMC-Vanderbilt']


***
<a id='ref_organs'></a>
#### Get all reference organs
<pre>
Accepted Parameters:
    cache - (boolean) (optional)
    token - (string) (optional)
</pre>

In [17]:
try:
    api_response = api_instance.reference_organs(cache = True)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

[{'@id': 'http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain',
 '@type': 'SpatialEntity',
 'creation_date': datetime.datetime(2022, 12, 14, 0, 0, tzinfo=tzutc()),
 'creator': 'Kristin Browne',
 'creator_first_name': 'Kristin',
 'creator_last_name': 'Browne',
 'dimension_units': 'millimeter',
 'label': 'Brain',
 'object': {'@id': 'http://purl.org/ccf/latest/ccf.owl#VHFAllenBrainObj',
            '@type': 'SpatialObjectReference',
            'file': 'https://ccf-ontology.hubmapconsortium.org/objects/v1.2/Allen_F_Brain.glb',
            'file_format': 'model/gltf-binary',
            'file_subpath': 'Allen_brain'},
 'reference_organ': 'http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain',
 'representation_of': 'http://purl.obolibrary.org/obo/UBERON_0000955',
 'rui_rank': 10.0,
 'sex': 'Female',
 'x_dimension': 136.3772335,
 'y_dimension': 146.09594200000004,
 'z_dimension': 167.0395271},
 {'@id': 'http://purl.org/ccf/latest/ccf.owl#VHMAllenBrain',
 '@type': 'SpatialEntity',
 'creation_date': 

***
<a id='3d_scene'></a>
#### Get all nodes to form the 3D scene for an organ
<pre>
Accepted Parameters:
    age - (MinMax) (optional) (min = 1.0; max = 110.0)
    bmi - (MinMax) (optional) (min = 13.0; max = 83.0)
    cache - (boolean)  (optional) (defaults to True)
    sex - (string)  (optional) (male, female, both)
    technologies - (string) (optional) (List of technologies - api_instance.technology_names)
    providers - (string) (optional) 
    ontology_terms - (string) (optional) 
    cell_type_terms - (string) (optional) 
    spatial - SpatialSearch(x, y, z, radius, target) (optional) 
    token - (string) (optional)
    organ-iri - (string) (required)
</pre>

In [18]:
age = MinMax(min=45.0, max=60.0)
bmi = MinMax(min=65.0, max=83.0)
cache = True
sex = "female"
technologies = []
providers = []
ontology_terms = ["http://purl.obolibrary.org/obo/UBERON_0000955",]
cell_type_terms = ["http://purl.obolibrary.org/obo/CL_0000000",] 
spatial = [SpatialSearch(
            x=84.0,
            y=146.0,
            z=53.0,
            radius=12.0,
            target="http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain",
        ),]
organ_iri = "http://purl.obolibrary.org/obo/UBERON_0004539"
token = ""

try:
    # Get aggregate results / statistics
    api_response = api_instance.reference_organ_scene(organ_iri=organ_iri, age=age, bmi=bmi, cache=cache, ontology_terms=ontology_terms, cell_type_terms=cell_type_terms, providers=providers, sex=sex, spatial=spatial, technologies=technologies, token=token
)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

[{'@id': 'http://purl.org/ccf/latest/ccf.owl#VHFRightKidneyV1.1',
 '@type': 'SpatialSceneNode',
 'color': [255.0, 255.0, 255.0, 255.0],
 'lighting': 'pbr',
 'opacity': 0.2,
 'reference_organ': 'http://purl.org/ccf/latest/ccf.owl#VHFRightKidneyV1.1',
 'representation_of': 'http://purl.obolibrary.org/obo/UBERON_0004539',
 'scenegraph': 'https://ccf-ontology.hubmapconsortium.org/objects/v1.2/VH_F_Kidney_R.glb',
 'scenegraph_node': 'VH_F_right_kidney',
 'tooltip': 'Right Kidney',
 'transform_matrix': [1.0,
                      0.0,
                      0.0,
                      0.0,
                      0.0,
                      1.0,
                      0.0,
                      0.0,
                      0.0,
                      0.0,
                      1.0,
                      0.0,
                      0.108721532,
                      -0.198595762,
                      0.134438053,
                      1.0],
 'unpickable': True},
 {'@id': 'http://purl.org/ccf/1.5/bf67c

***
<a id='nodes_3d'></a>
#### Get all nodes to form the 3D scene of reference body, organs, and tissues
<pre>
Accepted Parameters:
    age - (MinMax) (optional) (min = 1.0; max = 110.0)
    bmi - (MinMax) (optional) (min = 13.0; max = 83.0)
    cache - (boolean)  (optional) (defaults to True)
    sex - (string)  (optional) (male, female, both)
    technologies - (string) (optional) (List of technologies - api_instance.technology_names)
    providers - (string) (optional) 
    ontology_terms - (string) (optional) 
    cell_type_terms - (string) (optional) 
    spatial - SpatialSearch(x, y, z, radius, target) (optional) 
    token - (string) (optional)
</pre>

In [19]:
age = MinMax(min=45.0, max=60.0)
bmi = MinMax(min=65.0, max=83.0)
cache = True
sex = "female"
technologies = []
providers = []
ontology_terms = ["http://purl.obolibrary.org/obo/UBERON_0000955",]
cell_type_terms = ["http://purl.obolibrary.org/obo/CL_0000000",] 
spatial = [SpatialSearch(
            x=84.0,
            y=146.0,
            z=53.0,
            radius=12.0,
            target="http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain",
        ),]
token = ""

try:
    # Get aggregate results / statistics
    api_response = api_instance.scene(age=age, bmi=bmi, cache=cache, ontology_terms=ontology_terms, cell_type_terms=cell_type_terms, providers=providers, sex=sex, spatial=spatial, technologies=technologies, token=token
)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

[{'@id': 'http://purl.org/ccf/latest/ccf.owl#VHFSkinV1.1',
 '@type': 'SpatialSceneNode',
 'color': [255.0, 255.0, 255.0, 255.0],
 'lighting': 'pbr',
 'opacity': 0.5,
 'reference_organ': 'http://purl.org/ccf/latest/ccf.owl#VHFSkinV1.1',
 'representation_of': 'http://purl.obolibrary.org/obo/UBERON_0002097',
 'scenegraph': 'https://ccf-ontology.hubmapconsortium.org/objects/v1.3/3d-vh-f-skin.glb',
 'scenegraph_node': 'VH_F_skin',
 'tooltip': 'Skin',
 'transform_matrix': [1.0,
                      0.0,
                      0.0,
                      0.0,
                      0.0,
                      1.0,
                      0.0,
                      0.0,
                      0.0,
                      0.0,
                      1.0,
                      0.0,
                      0.0,
                      0.0,
                      0.0,
                      1.0],
 'unpickable': True,
 'zoom_based_opacity': False},
 {'@id': 'http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain',
 '@t

***
<a id='tech'></a>
#### Get technology names (for filtering)
<pre>
Accepted Parameters:
    cache - (boolean) (optional)
    token - (string) (optional)
</pre>

In [20]:
try:
    api_response = api_instance.technology_names(cache = False)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

['10x', 'AF', 'CODEX', 'IMC', 'LC', 'MALDI', 'OTHER', 'PAS']


***
<a id='tissue_block'></a>
#### Get Tissue Block Results
<pre>
Accepted Parameters:
    age - (MinMax) (optional) (min = 1.0; max = 110.0)
    bmi - (MinMax) (optional) (min = 13.0; max = 83.0)
    cache - (boolean)  (optional) (defaults to True)
    sex - (string)  (optional) (male, female, both)
    technologies - (string) (optional) (List of technologies - api_instance.technology_names)
    providers - (string) (optional) 
    ontology_terms - (string) (optional) 
    cell_type_terms - (string) (optional) 
    spatial - SpatialSearch(x, y, z, radius, target) (optional) 
    token - (string) (optional)
</pre>

In [22]:
age = MinMax(min=45.0, max=60.0)
bmi = MinMax(min=65.0, max=83.0)
cache = True
sex = "female"
technologies = []
providers = []
ontology_terms = ["http://purl.obolibrary.org/obo/UBERON_0000955",]
cell_type_terms = ["http://purl.obolibrary.org/obo/CL_0000000",] 
spatial = [SpatialSearch(
            x=84.0,
            y=146.0,
            z=53.0,
            radius=12.0,
            target="http://purl.org/ccf/latest/ccf.owl#VHFAllenBrain",
        ),]
token = ""

try:
    api_response = api_instance.tissue_blocks(age=age, bmi=bmi, cache=cache, ontology_terms=ontology_terms, cell_type_terms=cell_type_terms, providers=providers, sex=sex, spatial=spatial, technologies=technologies, token=token
)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

[{'@id': 'https://portal.brain-map.org/explore/seattle-alzheimers-disease#Human-MTG-10x_SEA-AD_Female_TissueBlock',
 '@type': 'Sample',
 'datasets': [{'@id': 'https://portal.brain-map.org/explore/seattle-alzheimers-disease#Human-MTG-10x_SEA-AD_Female_Dataset',
               '@type': 'Dataset',
               'label': 'SEA-AD_FEMALE_middle_temporal_gyrus',
               'link': 'https://portal.brain-map.org/explore/seattle-alzheimers-disease',
               'technology': 'OTHER',
               'thumbnail': 'assets/sea-ad/thumbnails/SEA-AD_logo_800x800.jpg'}],
 'description': '4 x 4 x 5 millimeter, 0.11 millimeter',
 'donor': {'@id': 'https://portal.brain-map.org/explore/seattle-alzheimers-disease#Human-MTG-10x_SEA-AD_Female_Donor',
           '@type': 'Donor',
           'description': 'Entered 2/20/2023, Rebecca Hodge, SEA-AD',
           'label': 'Middle Temporal Gyrus Female',
           'link': 'https://portal.brain-map.org/explore/seattle-alzheimers-disease',
           'provid

***
<a id='gtex_rui'></a>
#### Get all GTEx rui locations (if enabled)
<pre>
Accepted Parameters:
    cache - (boolean) (optional) 
</pre>

In [23]:
try: 
    api_response = api_instance.gtex_rui_locations(cache = False)
    pprint(api_response)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

{'@context': {'@base': 'http://purl.org/ccf/latest/ccf-entity.owl#',
              '@vocab': 'http://purl.org/ccf/latest/ccf-entity.owl#',
              'ccf': 'http://purl.org/ccf/latest/ccf.owl#',
              'cellTypeTerms': {'@id': 'has_cell_type_term', '@type': '@id'},
              'datasets': {'@id': 'has_dataset', '@type': '@id'},
              'description': 'rdfs:comment',
              'label': 'rdfs:label',
              'link': {'@id': 'rdfs:seeAlso', '@type': '@id'},
              'ontologyTerms': {'@id': 'has_ontology_term', '@type': '@id'},
              'rdfs': 'http://www.w3.org/2000/01/rdf-schema#',
              'rui_location': {'@id': 'has_spatial_entity', '@type': '@id'},
              'samples': {'@reverse': 'has_donor'},
              'sections': {'@id': 'has_tissue_section', '@type': '@id'},
              'thumbnail': {'@id': 'has_thumbnail'}},
 '@graph': [{'@id': 'https://gtexportal.org/home/tissue/Breast#FDonors',
             '@type': 'Donor',
            

***
<a id='token_usage'></a>
#### Token Usage

In [24]:
token = 'abbee123099245'
result = api_instance.db_status(token=token)
pprint(result)

{'checkback': 3600000,
 'load_time': 51365,
 'message': 'Database successfully loaded',
 'status': 'Ready'}
